In [1]:
import pandas as pd

In [2]:
activity = pd.read_csv("personDoingNormalActivity.csv")
no_activity = pd.read_csv("noPersonFanRunning.csv")

In [4]:
print("Number of columns: ", len(activity.columns))
activity.columns

Number of columns:  26


Index(['type', 'role', 'mac', 'rssi', 'rate', 'sig_mode', 'mcs', 'bandwidth',
       'smoothing', 'not_sounding', 'aggregation', 'stbc', 'fec_coding', 'sgi',
       'noise_floor', 'ampdu_cnt', 'channel', 'secondary_channel',
       'local_timestamp', 'ant', 'sig_len', 'rx_state', 'real_time_set',
       'real_timestamp', 'len', 'CSI_DATA'],
      dtype='object')

In [5]:
# No of columns with two or more values
exclude_cols = [len(activity[col].value_counts())<2 for col in activity.columns]
sum(exclude_cols)

16

In [6]:
select_cols = list(~pd.Series(exclude_cols))
activity.loc[:, select_cols]

rssi  mcs  stbc  sgi  noise_floor  ampdu_cnt  local_timestamp  \
0      -50    4     0    0          -98          1          6317181   
1      -49    4     1    0          -98          1          6573583   
2      -50    4     1    0          -98          1          9403668   
3      -49    4     1    0          -98          1         12439010   
4      -49    5     1    0          -98          1         12579050   
...    ...  ...   ...  ...          ...        ...              ...   
1892   -47    7     1    1          -97          1       2452894671   
1893   -47    7     1    1          -97          1       2452933114   
1894   -48    7     1    1          -97          1       2455477523   
1895   -52    7     1    1          -97          1       2457638456   
1896   -53    7     1    1          -97          1       2461254758   

      real_timestamp  len                                           CSI_DATA  
0            6.71656  256  [-106 -32 8 0 11 23 12 22 12 21 12 20 14 19 14...  
1            6.97191  384  [-106 -32 8 0 -2 8 -4 7 -6 8 -7 8 -8 10 -8 11 ...  
2            9.80248  384  [-106 -32 8 0 -6 -5 -4 -9 -3 -14 -4 -17 -4 -19...  
3           12.83740  384  [-106 -32 8 0 -7 -3 -6 -8 -6 -13 -7 -16 -8 -19...  
4           12.97740  384  [-106 -32 8 0 -6 -5 -4 -9 -3 -13 -3 -17 -2 -20...  
...              ...  ...                                                ...  
1892      2453.29000  384  [-106 -32 8 0 6 -10 10 -10 14 -12 17 -13 19 -1...  
1893      2453.40000  384  [-106 -32 8 0 -12 1 -15 -2 -19 -4 -22 -5 -25 -...  
1894      2455.88000  384  [-106 -32 8 0 -2 -12 -1 -16 0 -20 0 -23 -2 -26...  
1895      2458.04000  384  [-106 -32 8 0 20 -8 23 -10 25 -11 26 -13 26 -1...  
1896      2461.65000  384  [-106 -32 8 0 -19 13 -24 17 -27 21 -28 24 -29 ...  

[1897 rows x 10 columns]

In [7]:
activity["CSI_DATA"]

0       [-106 -32 8 0 11 23 12 22 12 21 12 20 14 19 14...
1       [-106 -32 8 0 -2 8 -4 7 -6 8 -7 8 -8 10 -8 11 ...
2       [-106 -32 8 0 -6 -5 -4 -9 -3 -14 -4 -17 -4 -19...
3       [-106 -32 8 0 -7 -3 -6 -8 -6 -13 -7 -16 -8 -19...
4       [-106 -32 8 0 -6 -5 -4 -9 -3 -13 -3 -17 -2 -20...
                              ...                        
1892    [-106 -32 8 0 6 -10 10 -10 14 -12 17 -13 19 -1...
1893    [-106 -32 8 0 -12 1 -15 -2 -19 -4 -22 -5 -25 -...
1894    [-106 -32 8 0 -2 -12 -1 -16 0 -20 0 -23 -2 -26...
1895    [-106 -32 8 0 20 -8 23 -10 25 -11 26 -13 26 -1...
1896    [-106 -32 8 0 -19 13 -24 17 -27 21 -28 24 -29 ...
Name: CSI_DATA, Length: 1897, dtype: object

In [8]:
activity["bandwidth"]

0       0
1       0
2       0
3       0
4       0
       ..
1892    0
1893    0
1894    0
1895    0
1896    0
Name: bandwidth, Length: 1897, dtype: int64

Channel state information (CSI) refers to the channel information of a Wi-Fi connection.
- In ESP32, this information consists of channel frequency responses of sub-carriers and is estimated when packets are received from the transmitter. 
- Each channel frequency response of sub-carrier is recorded by two bytes of signed characters.
- The first one is imaginary part and the second one is real part.
- There are up to three fields of channel frequency responses according to the type of received packet.
  - legacy long training field (LLTF), 
  - high throughput LTF (HT-LTF), and 
  - space time block code HT-LTF (STBC-HT-LTF). 
- For different types of packets which are received on channels with different state, the sub-carrier index and total bytes of signed characters of CSI are shown in the following table.

|        Channel     | Secondary Channel |  None   |         |      |
|:------------------:|:-----------------:|:-------:|:-------:|:-----|
| Packet Information | Signal Mode       | non HT  |  HT            |
|                    | Channel Bandwidth | 20MHz   | 20 MHz         |
|                    | STBC              | non STBC   | non STBC| STBC |
|Sub-carrier index   | LLTF              |    0 ~ 31, -32 ~ -1 |0 ~ 31, -32 ~ -1|0to31, -32to-1     |
|                    | HT-LTF            |-  | 0 ~ 31, -32 ~ -1  |0to31, -32to-1   |
|                    | STBC-HT-LTF       | -| -|0to31, -32to-1    |
|                    | Total bytes       | 128     |  256    |  384 |



384 bytes represents 64 subcarrier's Imag+Real part for LLTF, HT-LTF and STBC-HT-LTF.

In [12]:
activity["sig_mode"].unique()    # 1 represents High Throughput(HT)

array([1], dtype=int64)

In [13]:
activity["bandwidth"].unique()  # 0 represents 20MHz bandwidth

array([0], dtype=int64)

In [14]:
activity["secondary_channel"].unique()  # 0 represents No secondary channel

array([0], dtype=int64)

In [42]:
activity[activity["stbc"]==0]  # 0 represents non STBC

type role                mac  rssi  rate  sig_mode  mcs  bandwidth  \
0    CSI_DATA  STA  C2:DC:DC:2B:E5:05   -50    11         1    4          0   
304  CSI_DATA  STA  C2:DC:DC:2B:E5:05   -50    11         1    1          0   

     smoothing  not_sounding  ...  channel  secondary_channel  \
0            0             1  ...        1                  0   
304          0             1  ...        1                  0   

     local_timestamp  ant  sig_len  rx_state  real_time_set  real_timestamp  \
0            6317181    0      150         0              0         6.71656   
304        345997937    0      150         0              0       346.83000   

     len                                           CSI_DATA  
0    256  [-106 -32 8 0 11 23 12 22 12 21 12 20 14 19 14...  
304  256  [-106 -32 8 0 11 5 4 5 -2 7 -7 9 -11 12 -13 14...  

[2 rows x 26 columns]

The first data and 305th data has STBC(Space Time Block Code) so, they are of 256 bytes.
While rest are of 384 bytes.

### CSI Data Exploration

In [43]:
activity["CSI_DATA"][10]

'[-106 -32 8 0 -6 -1 -4 -6 -3 -11 -3 -16 -4 -20 -5 -24 -6 -26 -9 -27 -9 -27 -10 -26 -11 -25 -10 -21 -9 -18 -7 -14 -4 -10 -2 -6 2 -3 6 0 9 3 12 6 14 8 16 9 17 11 18 11 17 12 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 18 -2 23 -1 26 -1 30 0 30 0 32 0 31 0 29 1 25 1 21 2 16 2 10 3 4 3 -3 5 -9 6 -14 8 -20 10 -22 12 -25 15 -25 17 -27 19 -26 21 -24 20 -22 19 -19 18 -14 14 -77 0 -16 9 -16 9 -15 9 -15 10 -14 9 -14 10 -13 10 -12 10 -12 10 -12 10 -12 10 -11 10 -11 10 -11 10 -11 10 -11 10 -11 10 -11 9 -11 9 -11 8 -11 7 -11 7 -11 7 -11 6 -11 5 -11 4 -11 4 -11 2 0 0 0 0 0 0 0 0 0 0 0 0 0 0 -5 13 -7 13 -9 13 -10 12 -11 11 -12 11 -12 11 -13 11 -14 11 -15 10 -16 10 -17 8 -17 8 -17 8 -17 7 -17 7 -18 6 -18 7 -17 7 -17 7 -17 7 -17 8 -17 9 -17 8 -17 8 -16 8 -17 9 -16 9 -77 0 12 3 12 3 12 3 12 3 11 3 11 2 11 1 11 1 11 0 12 0 11 0 11 0 11 0 10 0 10 0 10 0 11 0 10 0 11 0 10 0 10 0 9 1 9 1 9 1 8 1 8 1 8 3 7 3 0 0 0 0 0 0 0 0 0 0 0 0 0 0 12 -4 12 -2 12 -1 13 0 13 1 13 2 13 2 13 3 13 4 14 5 13 6 13 6 12 6 12 7

In [44]:
str='112 -128 6 0 0 0 0 0 0 0 0 0 3 9 2 10 1 12 0 14 1 14 1 16 2 16 3 16 3 16 4 15 5 15 5 14 5 13 4 12 2 11 1 11 0 11 -1 11 -2 12 -3 13 -3 14 -3 15 -2 16 -1 17 0 17 1 17 0 0 2 15 2 14 2 14 1 12 0 12 -1 12 -2 12 -4 12 -4 13 -4 15 -4 16 -4 17 -3 18 -3 19 -1 19 0 19 1 18 2 17 1 16 2 15 0 14 -1 14 -2 13 -3 14 -4 15 -6 16 0 0 0 0 0 0 0 0 0 0'
vals = str.split(' ')
print(len(vals))

128


#### sig_mode

- 0: non HT(11bg) packet;
- 1: HT(11n) packet;
- 3: VHT(11ac) packet

#### mcs: Modulation Coding Scheme
If is HT(11n) packet, shows the modulation, range from 0 to 76(MSC0 ~ MCS76)

#### bandwidth: Channel Bandwidth of the packet. 
- 0: 20MHz
- 1: 40MHz


#### aggregation
Aggregation. 
- 0: MPDU packet
- 1: AMPDU packet
    
#### stbc
Space Time Block Code(STBC) 
- O: non STBC packet
- 1: STBC packet
        
#### fec_coding (Forward Error Correction)
Flag is set for 11n packets which are LDPC(low density parity check)

#### sgi
Short Guide Interval(SGI)
- 0: Long GI
- 1: Short GI

#### noise_floor
noise floor of Radio Frequency Module(RF). unit: dBm
    
#### channel
primary channel on which this packet is received


#### secondary_channel 
secondary channel on which this packet is received. 
- 0: none
- 1: above
- 2: below

#### timestamp
The local time when this packet is received. It is precise only if modem sleep or light sleep is not enabled. 
- unit: microsecond
    
#### ant (antenna number)
antenna numberfrom which this packet is received.
- 0: WiFi antenna 0
- 1: WiFi antenna 1

#### sig_len
length of packet including Frame Check Sequence(FCS)

#### rx_state
state of the packet.
- 0: no error 
- others: error numbers which are not public

#### len
length of CSI data


'mcs', 'bandwidth',
       'smoothing', 'not_sounding', 'aggregation', 'stbc', 'fec_coding', 'sgi',
       'noise_floor', 'ampdu_cnt', 'channel', 'secondary_channel',
       'local_timestamp', 'ant', 'sig_len', 'rx_state', 'real_time_set',
       'real_timestamp', 'len', 

### Wireless Signal Strength and Noise Levels


#### RSSI 
Received Signal Strength Indicator (RSSI) is a measurement of the power present in a received radio signal. 
- The RSSI is indicated by a negative dBm value. This value relates to the signal strength of the cellular signal from the tower to the modem. 
- The higher the number, the better the signal. The exact numbers vary between cellular carriers. 
-  However, -70 dBm and higher values usually equate to the modem being in an excellent coverage area. 
- The closer to 0 dBm, the stronger the signal.
- The RSSI is a relative value. Its measurement depends on the receiving device. 

|        RSSI        | Signal strength |                                                  Description                                                 |   |
|:------------------:|:---------------:|:------------------------------------------------------------------------------------------------------------:|---|
| > -65 dBm          | Excellent       | Strong signal with maximum data speeds                                                                       |   |
| -65 dBm to -75 dBm | Good            | Strong signal with good data speeds                                                                          |   |
| -75 dBm to -85 dBm | Fair            | Fair but useful, fast and reliable data speeds may be attained, but marginal data with drop-outs is possible |   |
| -85 dBm to -95 dBm | Poor            | Performance will drop drastically                                                                            |   |
| <= -95 dBm         | No signal       | Disconnection                                                                                                |   |


stbc	sgi	noise_floor	ampdu_cnt

#### STBC (Space-Time Block Coding) 
A method of transmitting a single data stream across multiple antennas for additional transmission redundancy. Some routers may support this advanced setting, use at your discretion.
- 0: non STBC packet
- 1: STBC packet

#### Short Guide Intervals (SGI, Short GI) - part of 802.11n specs. 
The "guard interval" is normally 800ns, and represents time spacing between symbols to prevent inter-symbol interference (ISI). 
- 0: Long GI
- 1: Short GI

It is not to be confused with the space between packets, which is the inter-frame space (IFS). In standard wireless environments, where multipath can be an issue, the "guard interval" is by default 800ns. 
- Turning on SGI can reduce that interval to 400ns. Only some vendors support SGI on 20MHz channels in the 2.4GHz spectrum. 
- Turning on SGI can increase wireless data rate by 11% by reducing idle time in environments that are not very noisy. 
- However, in noisy environments prone to multipath distortion, ISI would increase with SGI, reducing throughput. 


####  Signal Strength
The signal strength is the wireless signal power level received by the wireless client.

- Strong signal strength results in more reliable connections and higher speeds.
- Signal strength is represented in -dBm format (0 to -100). This is the power ratio in decibels (dB) of the measured power referenced to one milliwatt.
- The closer the value is to 0, the stronger the signal. For example, -41dBm is better signal strength than -61dBm.

#### Noise Level
The noise level indicates the amount of background noise in your environment.

- If the noise level is too high, it can result in degraded strength and performance for your wireless signal strength.
- Noise level is measured in -dBm format (0 to -100). This is the power ratio in decibels (dB) of the measured power referenced to one milliwatt.
- The closer the value to 0, the greater the noise level.
- Negative values indicate less background noise. For example, -96dBm is a lower noise level than -20dBm.

#### Signal to Noise Ratio
The signal-to-noise ratio (SNR) is the power ratio between the signal strength and the noise level.

- This value is represented as a +dBm value.
- In general, you should have a minimum of +25dBm signal-to-noise ratio. Lower values than +25dBm result in poor performance and speeds.
- For example:

    - If you have a -41dBm signal strength, and a -50dBm noise level, this results in a poor signal-to-noise ratio of +9dBm.
    - If you have a -41dBm signal strength, and a -96dBm noise level, this results in an excellent signal-to-noise ratio of +55dBm.

#### Noise Floor
The SNR is the difference between the received wireless signal and the noise floor. The noise floor is simply erroneous background transmissions that are emitted from either other devices that are too far away for the signal to be intelligible, or by devices that are inadvertently creating interference on the same frequency. 

- For example, if a client device's radio receives a signal at -75 dBm, and the noise floor is -90 dBm, then the effective SNR is 15 dB. This would then reflect as a signal strength of 15 dB for this wireless connection.

In [45]:
from IPython.display import Image
from IPython.core.display import HTML 
Image(url= "https://documentation.meraki.com/@api/deki/files/4251/clipboard_e8c4bdb9e8daf8c81cb963f4185979f69.png?revision=1")

The further a received signal is from the noise floor, the better the signal quality. Signals close to the noise floor can be subject to data corruption, which will result in retransmissions between the transmitter and receiver. This will degrade wireless throughput and latency as the retransmitted signals will take up airtime in the wireless environment.

#### Parse string to create integer list

In [46]:
import math

csi_string = activity["CSI_DATA"].to_list()
for i, value in enumerate(csi_string):
    imaginary = []
    real = []
    amplitudes = [] 
    phases = []
    # Remove [ and ]
    value = value.replace("[","")
    value = value.replace("]","")

    
    # Parse string to create integer list
    csi_raw = [int(x) for x in value.split(" ") if x != '']
    
    # Create list of imaginary and real numbers from CSI
    for item in range(len(csi_raw)):
        if item%2==0:
            imaginary.append(csi_raw[item])
        else:
            real.append(csi_raw[item])

    # Transform imaginary and real into amplitude and phase
    for k in range(int(len(csi_raw)//2)):
        amplitudes.append(round(math.sqrt(imaginary[k] ** 2 + real[k] ** 2),4))
        phases.append(round(math.atan2(imaginary[k], real[k]),4))

    print("-------------------")
    print("Csi_Amplitude#{}:".format(i), amplitudes)
    print("Csi_Phase#{}:    ".format(i), phases)
    print("-------------------")

-------------------
Csi_Amplitude#0: [110.7249, 8.0, 25.4951, 25.0599, 24.1868, 23.3238, 23.6008, 22.8035, 22.0227, 22.6716, 21.2603, 22.6716, 21.2603, 21.2132, 21.2132, 20.5183, 20.5183, 19.799, 19.105, 19.799, 19.105, 18.3848, 17.0294, 17.0294, 17.2047, 16.6433, 15.2643, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 20.8087, 21.095, 21.4709, 22.3607, 21.9317, 23.7697, 24.6982, 25.632, 25.0, 25.9615, 25.4951, 26.3059, 25.318, 25.1794, 25.318, 26.3059, 26.3059, 25.4951, 24.5153, 25.9615, 25.2982, 26.5707, 25.632, 25.632, 25.632, 25.632, 1.4142, 49.2443, 47.8539, 48.3011, 47.0106, 45.2769, 46.0435, 43.0116, 42.2019, 43.4166, 41.8688, 43.2782, 41.7732, 39.6232, 40.3113, 39.6232, 40.3609, 38.2099, 38.2099, 37.5366, 37.5366, 34.7131, 33.4215, 32.8024, 33.0151, 32.45, 31.3847, 30.0832, 29.1204, 1.4142, 1.4142, 1.4142, 1.4142, 0.0, 0.0, 0.0, 37.4833, 40.6079, 40.2244, 42.19, 42.0595, 43.8634, 43.4626, 45.31, 49.0408, 49.3356, 47.8017, 49.4773, 49.8197, 49.6488, 50.636, 49.366, 50.63

In [ ]:
val = activity["CSI_DATA"].to_list()

In [ ]:
import re
# val2 = re.findall(r"\[(.*)\]", val)[0]
val[0].replace("[","")

In [ ]:
x='[xram]'
x.replace("[","")